In [1]:
import cv2
import time

import glob
import os
from openpyxl import Workbook
from ultralytics import YOLO
from PIL import Image
import numpy as np
import pandas as pd
from openpyxl import load_workbook

### 人数カウント

In [2]:
day_files = sorted(glob.glob("/media/frog-takuma/imation i9/*"))
model = YOLO("model/yolov8x.pt") 
model.to("cuda:0")

GREEN = (0, 200, 0)
ORANGE = (0, 100, 255)
BLUE = (255, 100, 0)
conf_threshold = 0.90

all_data = {}

excel_filename = 'time_count_data.xlsx'

if not os.path.exists(excel_filename):
    # エクセルファイルが存在しない場合は新規作成
    workbook = Workbook()
    workbook.save(excel_filename)

try:
    existing_df = pd.read_excel(excel_filename)
except FileNotFoundError:
    existing_df = pd.DataFrame(columns=['year','month','day','hour','minute','Count'])

new_df = pd.DataFrame(columns=['year','month','day','hour','minute','Count'])

for df in day_files:
    hour_files = sorted(glob.glob(os.path.join(df,"*")))

    day_data = []
    sheet_name = df.split("/")[-1]


    for hf in hour_files:
        min_files = sorted(glob.glob(os.path.join(hf,"*")))
        print(len(min_files))

        for mf in min_files:
            
            print(mf)
            cap = cv2.VideoCapture(mf)

            if not cap.isOpened():
                print("Error: 動画ファイルを開くことができません。")
                exit()

            # フレームを一つずつ読み取る
            while cap.isOpened():
                ret, frame = cap.read()


                start_time = time.time()
                results = model(frame, conf=0.5, verbose=False)
                end_time = time.time()
                execution_time = end_time - start_time

                print("実行時間: {}秒".format(execution_time))

                detections = results[0].boxes.data
                detections = detections.to("cpu").numpy()
                class_0_count = np.sum(detections[:, -1] == 0)

                year = mf.split("/")[-3][:4]
                month = mf.split("/")[-3][4:6]
                day = mf.split("/")[-3][6:8]
                hour = mf.split("/")[-2]
                minute = mf.split("/")[-1][:2]
                second = "00"

                counts_over_threshold = 0
                counts_under_threshold = 0

                for x0, y0, x1, y1, conf, class_id in detections:
                    x0 = int(x0)
                    y0 = int(y0)
                    x1 = int(x1)
                    y1 = int(y1)
                    
                    if conf > conf_threshold:
                        color = GREEN
                        counts_over_threshold += 1
                    else:
                        color = ORANGE
                        counts_under_threshold += 1

                    if class_id == 0:
                        cv2.rectangle(frame,
                                    pt1 = (int(x0), int(y0)),
                                    pt2 = (int(x1), int(y1)),
                                    color = color,
                                    thickness = 2,
                                    lineType = cv2.LINE_AA)
                        
                        cv2.putText(frame,
                                    text = f"{conf:.2f}",
                                    org = (int(x0), int(y0)-5),
                                    fontFace = cv2.FONT_HERSHEY_SIMPLEX,
                                    fontScale = 0.8,
                                    color = color,
                                    thickness = 2,
                                    lineType = cv2.LINE_AA)

                save_dir = os.path.join("save_img", f"{year}{month}{day}")
                os.makedirs(save_dir, exist_ok=True)

                filename = f"{year}{month}{day}{hour}{minute}{second}_{class_0_count}.jpg"
                filepath = os.path.join(save_dir, filename)
                print(filepath)       

                frame_rgb = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)
                pil_img = Image.fromarray(frame_rgb)
                #pil_img.save(filepath)   

                new_data = {
                    'ymd': f"{year}/{month}/{day}",  
                    'hm': f"{hour}:{minute}",
                    'Count': class_0_count  
                }
                """
                new_data = {
                    'ym': year,  
                    '': month,  
                    'day': day,  
                    'hour': hour,
                    'minute': minute,    
                    'Count': class_0_count  
                }
                """
                day_data.append(new_data)


                break
        
    new_df = pd.DataFrame(day_data)

    try:
        book = load_workbook(excel_filename)
        if sheet_name in book.sheetnames:
            # 既存のシートを読み込む
            existing_df = pd.read_excel(excel_filename, sheet_name=sheet_name)
            # 既存のデータに新しいデータを追加
            updated_df = pd.concat([existing_df, new_df], ignore_index=True)
        else:
            # 新しいシートを作成
            updated_df = new_df
    except FileNotFoundError:
        # ファイルが存在しない場合、新しいデータフレームをそのまま使用
        updated_df = new_df

    with pd.ExcelWriter(excel_filename, engine='openpyxl', mode='a' if 'book' in locals() else 'w', if_sheet_exists='replace') as writer:
        updated_df.to_excel(writer, sheet_name=sheet_name, index=False)        




            #cap = cv2.VideoCapture(min_files)
            

100%|██████████| 131M/131M [00:11<00:00, 11.7MB/s] 


60
/media/frog-takuma/imation i9/20240527/00/00.mp4
実行時間: 1.4922106266021729秒
save_img/20240527/20240527000000_0.jpg
/media/frog-takuma/imation i9/20240527/00/01.mp4
実行時間: 0.013300895690917969秒
save_img/20240527/20240527000100_0.jpg
/media/frog-takuma/imation i9/20240527/00/02.mp4
実行時間: 0.012570858001708984秒
save_img/20240527/20240527000200_0.jpg
/media/frog-takuma/imation i9/20240527/00/03.mp4
実行時間: 0.012284040451049805秒
save_img/20240527/20240527000300_0.jpg
/media/frog-takuma/imation i9/20240527/00/04.mp4
実行時間: 0.012583494186401367秒
save_img/20240527/20240527000400_0.jpg
/media/frog-takuma/imation i9/20240527/00/05.mp4
実行時間: 0.012572288513183594秒
save_img/20240527/20240527000500_0.jpg
/media/frog-takuma/imation i9/20240527/00/06.mp4
実行時間: 0.1067495346069336秒
save_img/20240527/20240527000600_0.jpg
/media/frog-takuma/imation i9/20240527/00/07.mp4
実行時間: 0.012598991394042969秒
save_img/20240527/20240527000700_0.jpg
/media/frog-takuma/imation i9/20240527/00/08.mp4
実行時間: 0.0133650302886962

In [2]:
import os
import datetime
import csv
import urllib.request
from bs4 import BeautifulSoup
import pandas as pd

def str2float(weather_data):
    try:
        return float(weather_data)
    except:
        return 0

def scraping(url, date):

    # 気象データのページを取得
    html = urllib.request.urlopen(url).read()
    soup = BeautifulSoup(html, 'html.parser')
    trs = soup.find("table", { "class" : "data2_s" })

    data_list = []
    data_list_per_hour = []

    # table の中身を取得
    for tr in trs.findAll('tr')[2:]:
        tds = tr.findAll('td')

        if tds[1].string == None:
            break

        data_list.append(date)
        data_list.append(tds[0].string)
        data_list.append(str2float(tds[1].string))
        data_list.append(str2float(tds[2].string))
        data_list.append(str2float(tds[3].string))
        data_list.append(str2float(tds[4].string))
        data_list.append(str2float(tds[5].string))
        data_list.append(str2float(tds[6].string))
        data_list.append(str2float(tds[7].string))
        data_list.append(str2float(tds[8].string))
        data_list.append(str2float(tds[9].string))
        data_list.append(str2float(tds[10].string))
        data_list.append(str2float(tds[11].string))
        data_list.append(str2float(tds[12].string))
        data_list.append(str2float(tds[13].string))

        data_list_per_hour.append(data_list)

        data_list = []

    return data_list_per_hour

def create_excel():
    # 出力ファイル名
    output_file = "weather.xlsx"

    # データ取得開始・終了日
    start_date = datetime.date(2024, 5, 27)
    end_date   = datetime.date(2024, 7, 12)

    # CSV の列
    columns = ["年月日", "時間", "気圧（現地）", "気圧（海面）",
               "降水量", "気温", "露点湿度", "蒸気圧", "湿度",
               "風速", "風向", "日照時間", "全天日射量", "降雪", "積雪"]

    # ExcelWriterオブジェクトを作成
    writer = pd.ExcelWriter(output_file, engine='xlsxwriter')

    date = start_date
    while date != end_date + datetime.timedelta(1):

        # 対象url（今回は東京）
        url = "http://www.data.jma.go.jp/obd/stats/etrn/view/hourly_s1.php?" \
              "prec_no=72&block_no=47890&year=%d&month=%d&day=%d&view=" % (date.year, date.month, date.day)

        data_per_day = scraping(url, date)

        # DataFrameに変換
        df = pd.DataFrame(data_per_day, columns=columns)

        # シート名を指定してExcelファイルに書き込み
        sheet_name = date.strftime("%Y%m%d")
        df.to_excel(writer, sheet_name=sheet_name, index=False)

        date += datetime.timedelta(1)

    # Excelファイルを保存
    writer.save()

if __name__ == '__main__':
    create_excel()


In [ ]:
import pandas as pd
import matplotlib.pyplot as plt

# Load the data
time_count_data = pd.read_excel('/mnt/data/time_count_data_v3.xlsx')
weather_data = pd.read_csv('weather.csv')

# Extract relevant columns
time_count_data['日付'] = pd.to_datetime(time_count_data['時間']).dt.date
weather_data['日付'] = pd.to_datetime(weather_data['時間']).dt.date

# Merge datasets on the '日付' and '時間' columns
merged_data = pd.merge(time_count_data, weather_data, on=['日付', '時間'])

# Extract unique dates
unique_dates = merged_data['日付'].unique()

YOLOv9